In [ ]:
!pip install tsai

     |████████████████████████████████| 234 kB 5.6 MB/s 
     |████████████████████████████████| 189 kB 47.4 MB/s 
     |████████████████████████████████| 2.5 MB 48.1 MB/s 
     |████████████████████████████████| 55 kB 4.1 MB/s 
  Attempting uninstall: fastai
    Found existing installation: fastai 1.0.61
    Uninstalling fastai-1.0.61:
      Successfully uninstalled fastai-1.0.61


需要修改一下/usr/local/lib/python3.7/dist-packages/tsai-0.2.26-py3.7.egg/tsai/models/utils.py这里的内容。添加一个NewModel或者之类的东西。再次手动增加内容。
后续可以考虑添加对应的包，直接在安装的时候成功。
同时如果针对LSTM-FCN，需要添加一个参数输入的内容

In [ ]:
from tsai.all import *
computer_setup()


os             : Linux-5.4.144+-x86_64-with-Ubuntu-18.04-bionic
python         : 3.7.12
tsai           : 0.3.0
fastai         : 2.5.3
fastcore       : 1.3.29
torch          : 1.10.0+cu111
n_cpus         : 2
device         : cuda (Tesla K80)


In [ ]:
# coding:UTF-8
# V2, ResNet Imporve


from tsai.imports import *
from tsai.utils import *
from torch.nn.init import normal_
from fastai.torch_core import Module
from fastai.layers import *
from torch.nn.utils import weight_norm, spectral_norm

Convolution = [8, 16, 32, 64, 128, 256]
# ZeroOp, 默认
# MaxPooling, 默认
# Dropout, 0-0.5之间
# Activate = {1: 'softmax', 2: 'elu', 3: 'Relu', 4: 'selu', 5: 'sigmoid'}
Activate = ['softmax', 'elu', 'Relu', 'selu', 'sigmoid']
Dense = [8, 16, 32, 64, 128, 256]


# -------------------------------------------
# ResNet相关内容
# 读懂ResNet
# Cell
class ResBlock(Module):
    def __init__(self, ni, nf, kss=[7, 5, 3]):
        # 搞定
        self.convblock1 = ConvBlock(ni, nf, kss[0])
        # 搞定
        self.convblock2 = ConvBlock(nf, nf, kss[1])
        # 搞定
        self.convblock3 = ConvBlock(nf, nf, kss[2], act=None)

        # expand channels for the sum if necessary
        # 这里的这种定义是想省点事。所以才使用这种方法。
        # 对于前两个残差block，就是ConvBlock
        # 对于最后一个残差block，就是一个BN1d
        self.shortcut = BN1d(ni) if ni == nf else ConvBlock(ni, nf, 1, act=None)

        # add
        self.add = Add()
        # 搞定
        self.act = nn.ReLU()

    def forward(self, x):
        res = x
        x = self.convblock1(x)
        x = self.convblock2(x)
        x = self.convblock3(x)
        x = self.add(x, self.shortcut(res))
        x = self.act(x)
        return x


class Modify_ResNet(Module):
    def __init__(self, c_in, c_out, Phenotype, batch_size):
        # if Phenotype: print(Phenotype)
        # else: assert 'Phenotype loss'
        # 显示性状
        # print(Phenotype)

        nf = 64
        kss = [7, 5, 3]
        front_output = nf * 2
        self.resblock1 = ResBlock(c_in, nf, kss=kss)
        self.resblock2 = ResBlock(nf, nf * 2, kss=kss)
        self.resblock3 = ResBlock(nf * 2, nf * 2, kss=kss)
        
        self.add_layer1, front_output = self._make_layer(Phenotype[0], front_output)
        self.add_layer2, front_output = self._make_layer(Phenotype[1], front_output)
        self.add_layer3, front_output = self._make_layer(Phenotype[2], front_output)
        self.add_layer4, front_output = self._make_layer(Phenotype[3], front_output)
        self.add_layer5, front_output = self._make_layer(Phenotype[4], front_output)
        self.add_layer6, front_output = self._make_layer(Phenotype[5], front_output)
        self.add_layer7, front_output = self._make_layer(Phenotype[6], front_output)
        self.add_layer8, front_output = self._make_layer(Phenotype[7], front_output)
        self.add_layer9, front_output = self._make_layer(Phenotype[8], front_output)
        self.add_layer10, front_output = self._make_layer(Phenotype[9], front_output)
        self.add_layer11, front_output = self._make_layer(Phenotype[10], front_output)
        self.add_layer12, front_output = self._make_layer(Phenotype[11], front_output)
        self.add_layer13, front_output = self._make_layer(Phenotype[12], front_output)
        self.add_layer14, front_output = self._make_layer(Phenotype[13], front_output)
        self.add_layer15, front_output = self._make_layer(Phenotype[14], front_output)

        # 一个池化
        self.gap = nn.AdaptiveAvgPool1d(1)

        # 减去末端张量
        self.squeeze = Squeeze(-1)

        # 全连接
        # self.fc = nn.Linear(nf * 2, c_out)
        self.fc = nn.Linear(front_output, c_out)

    def _make_layer(self, Phenotype, front_output):
        if Phenotype[0] == 0:  # conv
            out_size = Convolution[int(Phenotype[1])]            
            # print(f"conv{out_size}")
            return ConvBlock(front_output, out_size, 3), out_size
        
        elif Phenotype[0] == 1:  # ZeroOp
            # print("ZeroOp")
            return 0, front_output

        elif Phenotype[0] == 2:  # Maxpooling, Pooling size = 3, zero padding.
            # print(f"Maxpooling and unpooling")
            return nn.MaxPool1d(kernel_size=3, stride=1, padding=0, return_indices=True), front_output

        elif Phenotype[0] == 3:  # Dropout
            dropout_rate = Phenotype[1]
            # print(f"Dropout")
            return nn.Dropout(dropout_rate), front_output

        elif Phenotype[0] == 4: # Activate
            if Phenotype[1] == 0:
                act = nn.Softmax()
            elif Phenotype[1] == 1:
                act = nn.ELU()
            elif Phenotype[1] == 2:
                act = nn.ReLU()
            elif Phenotype[1] == 3:
                act = nn.SELU()
            elif Phenotype[1] == 4:
                act = nn.Sigmoid()
            # print(f"Acticate")
            return act, front_output

        elif Phenotype[0] == 5: # FC
            out_size = Dense[int(Phenotype[1])]
            # print(f"FC{out_size}")
            return nn.Linear(front_output, out_size), out_size
            


    def forward(self, x):
        x = self.resblock1(x)
        x = self.resblock2(x)
        # print("after resblock2 size", x.shape)
        x = self.resblock3(x)
        # print("after resblock3 size", x.shape)

        if self.add_layer1 != 0:
            if isinstance(self.add_layer1, nn.MaxPool1d):
                x, indices = self.add_layer1(x)
                x = nn.MaxUnpool1d(self.add_layer1.kernel_size, self.add_layer1.stride)(x, indices)
            elif isinstance(self.add_layer1, nn.Linear):
                x = torch.transpose(x, 1, 2)
                x = self.add_layer1(x)
                x = torch.transpose(x, 1, 2)
            else:
                x = self.add_layer1(x)  
  
        if self.add_layer2 != 0:
            if isinstance(self.add_layer2, nn.MaxPool1d):
                x, indices = self.add_layer2(x)
                x = nn.MaxUnpool1d(self.add_layer2.kernel_size, self.add_layer2.stride)(x, indices)
            elif isinstance(self.add_layer2, nn.Linear):
                x = torch.transpose(x, 1, 2)
                x = self.add_layer2(x)
                x = torch.transpose(x, 1, 2)
            else:
                x = self.add_layer2(x)  
          
        if self.add_layer3 != 0:
          if isinstance(self.add_layer3, nn.MaxPool1d):
              x, indices = self.add_layer3(x)
              x = nn.MaxUnpool1d(self.add_layer3.kernel_size, self.add_layer3.stride)(x, indices)
          elif isinstance(self.add_layer3, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer3(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer3(x)  
        
        if self.add_layer4 != 0:
          if isinstance(self.add_layer4, nn.MaxPool1d):
              x, indices = self.add_layer4(x)
              x = nn.MaxUnpool1d(self.add_layer4.kernel_size, self.add_layer4.stride)(x, indices)
          elif isinstance(self.add_layer4, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer4(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer4(x)  
        
        if self.add_layer5 != 0:
          if isinstance(self.add_layer5, nn.MaxPool1d):
              x, indices = self.add_layer5(x)
              x = nn.MaxUnpool1d(self.add_layer5.kernel_size, self.add_layer5.stride)(x, indices)
          elif isinstance(self.add_layer5, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer5(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer5(x)  
        
        if self.add_layer6 != 0:
          if isinstance(self.add_layer6, nn.MaxPool1d):
              x, indices = self.add_layer6(x)
              x = nn.MaxUnpool1d(self.add_layer6.kernel_size, self.add_layer6.stride)(x, indices)
          elif isinstance(self.add_layer6, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer6(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer6(x)  
        
        if self.add_layer7 != 0:
          if isinstance(self.add_layer7, nn.MaxPool1d):
              x, indices = self.add_layer7(x)
              x = nn.MaxUnpool1d(self.add_layer7.kernel_size, self.add_layer7.stride)(x, indices)
          elif isinstance(self.add_layer7, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer7(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer7(x)  
        
        if self.add_layer8 != 0:
          if isinstance(self.add_layer8, nn.MaxPool1d):
              x, indices = self.add_layer8(x)
              x = nn.MaxUnpool1d(self.add_layer8.kernel_size, self.add_layer8.stride)(x, indices)
          elif isinstance(self.add_layer8, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer8(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer8(x)  
        
        if self.add_layer9 != 0:
          if isinstance(self.add_layer9, nn.MaxPool1d):
              x, indices = self.add_layer9(x)
              x = nn.MaxUnpool1d(self.add_layer9.kernel_size, self.add_layer9.stride)(x, indices)
          elif isinstance(self.add_layer9, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer9(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer9(x)  
        
        if self.add_layer10 != 0:
          if isinstance(self.add_layer10, nn.MaxPool1d):
              x, indices = self.add_layer10(x)
              x = nn.MaxUnpool1d(self.add_layer10.kernel_size, self.add_layer10.stride)(x, indices)
          elif isinstance(self.add_layer10, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer10(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer10(x)  
        
        if self.add_layer11 != 0:
          if isinstance(self.add_layer11, nn.MaxPool1d):
              x, indices = self.add_layer11(x)
              x = nn.MaxUnpool1d(self.add_layer11.kernel_size, self.add_layer11.stride)(x, indices)
          elif isinstance(self.add_layer11, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer11(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer11(x)  
        
        if self.add_layer12 != 0:
          if isinstance(self.add_layer12, nn.MaxPool1d):
              x, indices = self.add_layer12(x)
              x = nn.MaxUnpool1d(self.add_layer12.kernel_size, self.add_layer12.stride)(x, indices)
          elif isinstance(self.add_layer12, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer12(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer12(x)  
        
        if self.add_layer13 != 0:
          if isinstance(self.add_layer13, nn.MaxPool1d):
              x, indices = self.add_layer13(x)
              x = nn.MaxUnpool1d(self.add_layer13.kernel_size, self.add_layer13.stride)(x, indices)
          elif isinstance(self.add_layer13, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer13(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer13(x)  
        
        if self.add_layer14 != 0:
          if isinstance(self.add_layer14, nn.MaxPool1d):
              x, indices = self.add_layer14(x)
              x = nn.MaxUnpool1d(self.add_layer14.kernel_size, self.add_layer14.stride)(x, indices)
          elif isinstance(self.add_layer14, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer14(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer14(x)  
        
        if self.add_layer15 != 0:
          if isinstance(self.add_layer15, nn.MaxPool1d):
              x, indices = self.add_layer15(x)
              x = nn.MaxUnpool1d(self.add_layer15.kernel_size, self.add_layer15.stride)(x, indices)
          elif isinstance(self.add_layer15, nn.Linear):
              x = torch.transpose(x, 1, 2)
              x = self.add_layer15(x)
              x = torch.transpose(x, 1, 2)
          else:
              x = self.add_layer15(x)  
          

        x = self.squeeze(self.gap(x))
        x = self.fc(x)
        return x

In [ ]:
# coding:UTF-8
# V2, ResNet Imporve
# 3.4.2022 run data, 8hours


from __future__ import division
from numpy import *
import random as rd

NP = 4
size = 15
xMin = -10
xMax = 10
F = 0.8
CR = 0.5
LAYER_THRESHOLD = 0.9
GEN_MAX = 10
TRAIN_EPOCHES = 80

Convolution = [8, 16, 32, 64, 128, 256]
# ZeroOp, 默认
# MaxPooling, 默认
# Dropout, 0-0.5之间
# Activate = {1: 'softmax', 2: 'elu', 3: 'Relu', 4: 'selu', 5: 'sigmoid'}
Activate = ['softmax', 'elu', 'Relu', 'selu', 'sigmoid']
Dense = [4, 16, 32, 64, 128, 256]


# fetch data:
dsid = 'Adiac' 
bs = 64
X, y, splits = get_UCR_data(dsid, return_split=False)
print(X.shape)
tfms  = [None, [Categorize()]]
dsets = TSDatasets(X, y, tfms=tfms, splits=splits)
dls   = TSDataLoaders.from_dsets(dsets.train, dsets.valid, bs=[bs, bs*2])



# 完成
def translate_architecture(Individual, display=False):
    m, n = shape(Individual)
    Actual_structure = zeros((m, n))
    layers = []
    # 15 * 2
    for i in range(m):
        if Individual[i][0] == 0: # conv
            single_layer = ["conv"]
            single_layer.append(Convolution[int(Individual[i][1] * 6)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 6)]
        elif Individual[i][0] == 1: # ZeroOp
            single_layer = ["ZeroOp"]
            single_layer.append("Default")
            Actual_structure[i] = [Individual[i][0], Individual[i][1]]
        elif Individual[i][0] == 2: # Maxpooling
            single_layer = ["Maxpooling"]
            single_layer.append("Default")
            Actual_structure[i] = [Individual[i][0], Individual[i][1]]
        elif Individual[i][0] == 3:
            single_layer = ["Dropout"]
            single_layer.append(0.5*Individual[i][1])
            Actual_structure[i] = [Individual[i][0], 0.5*Individual[i][1]]
        elif Individual[i][0] == 4:
            single_layer = ["Activate"]
            single_layer.append(Activate[int(Individual[i][1] * 5)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 5)]
        elif Individual[i][0] == 5:
            single_layer = ["Dense"]
            single_layer.append(Dense[int(Individual[i][1] * 6)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 6)]
        layers.append(single_layer)
    if display:
        print(f"structure is {layers}")
    return Actual_structure


def GetModel(Phenotype):    
    m, n = shape(Phenotype)
    arch = Modify_ResNet
    print(arch.__name__)
    model = create_model(arch, dls=dls, Phenotype=Phenotype, batch_size=bs)
    print(model)
    return model


def getPred(Phenotype):
    
    # 训练
    model = GetModel(Phenotype)
    # return 1

    learn = Learner(dls, model,  metrics=accuracy)
    start = time.time()
    learn.fit_one_cycle(TRAIN_EPOCHES, 1e-3)
    elapsed = time.time() - start
    vals = learn.recorder.values[-1]
    # results = pd.DataFrame(columns=['arch', 'hyperparams', 'total params', 'train loss', 'valid loss', 'accuracy', 'time'])
    # results.loc[1] = [arch.__name__, {}, total_params(model)[0], vals[0], vals[1], vals[2], int(elapsed)]
    # results.sort_values(by='accuracy', ascending=False, ignore_index=True, inplace=True)
    # clear_output()
    # display(results)
    return vals[2]
    
    # return 1


# # 计算适应值函数
def calFitness(Individual):
    # Translate Individual Architecture
    # 目标: pred
    # Phenotype = translate_architecture(Individual, display=True)
    Phenotype = translate_architecture(Individual)


    # print("Phenotype after translate")
    # print(Phenotype)
    # 从getPred中获取对应的prediction
    fitness = getPred(Phenotype)

    return fitness



# 完成
def mutation(X_Parent, F, LAYER_THRESHOLD):
    # Mutate for Neural network
    print(shape(X_Parent))
    m, n, k = shape(X_Parent)
    # print()
    XMutationTmp = zeros((m, n, k))

    # 对于此时来说，需要额外设定一个layer_rate, 如果大于layer_rate，那么就mutate，layer，如果小于layer_rate，调整parameter。

    count = 0

    for i in range(m):
        r1 = 0
        r2 = 0
        r3 = 0
        while r1 == i or r2 == i or r3 == i or r1 == r2 or r1 == r3 or r2 == r3:
            r1 = rd.randint(0, m - 1)
            r2 = rd.randint(0, m - 1)
            r3 = rd.randint(0, m - 1)

        for j in range(n):
            # 如果需要修改layer
            layer_change = rd.random()
            if (layer_change > LAYER_THRESHOLD):
                changed_layer = rd.randint(0, 5)
                XMutationTmp[i, j] = [changed_layer, rd.random()]
                continue

            # 如果不需要修改layer， 这里会有点担心会产生越界

            # 首先要看一下此时是不是同一类的r1, r2, r3，因为真的太严格了，所以就是说mutate也要考虑基因突变
            # 如果r1、r2都满足的话，就可以按照操作开始变换。
            if X_Parent[r1, j, 0] == X_Parent[r2, j, 0] or X_Parent[r1, j, 0] == X_Parent[r3, j, 0]:
                # 用6完成一次取余操作
                XMutationTmp[i, j] = [X_Parent[r1, j, 0], (X_Parent[r1, j, 1] + F * (X_Parent[r2, j, 1] - X_Parent[r3, j, 1])) % 1]
                # print("差分操作完成", count)
                # count += 1
            else:
                XMutationTmp[i, j] = X_Parent[i, j]
    # print()
    return XMutationTmp


# 完成
def crossover(X_Parent, XMutationTmp, CR):
    # Binomial strategy
    # 按照CR crossrate完成修正增

    m, n, k = shape(X_Parent)
    X_Crossover = zeros((m, n, k))

    for i in range(m):
        for j in range(n):
            r = rd.random()
            if r <= CR:
                X_Crossover[i, j] = XMutationTmp[i, j]
            else:
                X_Crossover[i, j] = X_Parent[i, j]
    return X_Crossover


# 完成
def selection(X_Parent, XCrossover, fitnessVal):
    m, n, k = shape(X_Parent)
    print("Parent_fitness:", fitnessVal)
    fitnessCrossOverVal = zeros((m, 1))
    for i in range(m):
        print(f"第{i}个变异个体")
        fitnessCrossOverVal[i, 0] = calFitness(XCrossover[i])
        if (fitnessCrossOverVal[i, 0] > fitnessVal[i, 0]):
            for j in range(n):
                X_Parent[i, j] = XCrossover[i, j]
            fitnessVal[i, 0] = fitnessCrossOverVal[i, 0]
    return X_Parent, fitnessVal


# 完成
def saveBest(XTemp, fitnessVal):
    m = shape(fitnessVal)[0]
    print("After selection", fitnessVal)
    tmp = 0
    for i in range(1, m):
        if (fitnessVal[tmp] > fitnessVal[i]):
            tmp = i

    print("Round Best:")
    print(fitnessVal[tmp][0])
    translate_architecture(XTemp[tmp], display=True)


# # 正文代码----------------

if __name__ == '__main__':

    # 初始化
    XTemp = zeros((NP, size, 2))
    # 构造对应的NP = 50, 基因长度size = 15, 每个size里包含的一个超参数，长度为2

    for i in range(NP):
        for j in range(size):
            # 初始化规则：对于每个XTemp[i, j]，[x, y]相当于初始化此时的类型x以及参数y
            # Conv的类型:          0; Conv的参数: [8, 16, 32, 64, 128, 256]; 一共6个参数，在乘以对应比例后截取整数部
            # ZeroOP的类型:        1; 没有参数
            # Maxpooling的类型:    2; MaxPooling，没有参数
            # Dropout的类型:       3; Dropout的参数: [0, 0.5]; random后乘以0.5
            # Activate的类型:      4; Activate的参数: ['softmax', 'elu', 'Relu', 'selu', 'sigmoid']; 5个参数，random后乘比例
            # Dense的类型:         5; Dense的参数: [4, 16, 32, 64, 128, 256]; 6个参数, random后乘比例。
            type = rd.randint(0, 5)
            XTemp[i, j] = [type, rd.random()]
    print("完成初始化")

    # 计算初始适应值
    fitnessVal = zeros((NP, 1))
    for i in range(NP):
        print(f"第{i}个个体")
        fitnessVal[i, 0] = calFitness(XTemp[i])


    gen = 0
    while gen <= GEN_MAX:
        print("")
        print(f"Generation {gen}")
        # translate_architecture(XTemp[0], display=True)
        # mutate完成
        XMutationTmp = mutation(XTemp, F, LAYER_THRESHOLD)
        print("Mutate 完成")
        # translate_architecture(XMutationTmp[0], display=True)

        print("Crossover完成")
        XCrossover = crossover(XTemp, XMutationTmp, CR)
        # translate_architecture(XCrossover[0], display=True)

        XTemp, fitnessVal = selection(XTemp, XCrossover, fitnessVal)
        print("Select完成")
        # calFitness(XCrossover[0])
        saveBest(XTemp, fitnessVal)

        gen += 1

(781, 1, 176)
完成初始化
Modify_ResNet
[[1.         0.70663314]
 [3.         0.0476495 ]
 [4.         4.        ]
 [2.         0.39305468]
 [4.         0.        ]
 [1.         0.27686911]
 [0.         3.        ]
 [4.         3.        ]
 [5.         2.        ]
 [4.         0.        ]
 [4.         1.        ]
 [0.         0.        ]
 [3.         0.05228123]
 [5.         1.        ]
 [1.         0.81196033]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,

Modify_ResNet
[[4.         4.        ]
 [1.         0.15660281]
 [5.         5.        ]
 [0.         5.        ]
 [5.         5.        ]
 [5.         2.        ]
 [4.         1.        ]
 [4.         4.        ]
 [0.         0.        ]
 [0.         1.        ]
 [0.         0.        ]
 [0.         4.        ]
 [3.         0.10035995]
 [5.         2.        ]
 [5.         0.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
     

Modify_ResNet
[[3.         0.4722913 ]
 [2.         0.05436458]
 [1.         0.55673464]
 [4.         3.        ]
 [5.         3.        ]
 [1.         0.01885868]
 [2.         0.85061654]
 [2.         0.20226234]
 [3.         0.18662559]
 [1.         0.18592979]
 [0.         0.        ]
 [1.         0.04409989]
 [1.         0.20277357]
 [0.         5.        ]
 [4.         2.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
     

Modify_ResNet
[[3.         0.16683468]
 [2.         0.5224256 ]
 [4.         3.        ]
 [5.         1.        ]
 [0.         4.        ]
 [0.         5.        ]
 [2.         0.31793653]
 [0.         0.        ]
 [5.         0.        ]
 [2.         0.54240058]
 [5.         3.        ]
 [5.         4.        ]
 [3.         0.0168752 ]
 [2.         0.02664537]
 [0.         2.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
     


Generation 0
(4, 15, 2)
Mutate 完成
Crossover完成
Modify_ResNet
[[1.         0.70663314]
 [2.         0.76170635]
 [4.         4.        ]
 [2.         0.39305468]
 [4.         0.        ]
 [1.         0.27686911]
 [0.         3.        ]
 [4.         3.        ]
 [5.         2.        ]
 [5.         0.        ]
 [4.         1.        ]
 [0.         0.        ]
 [3.         0.05228123]
 [5.         1.        ]
 [1.         0.81196033]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,

...

Select完成
Round Best:
0.260869562625885
structure is [['Dropout', 0.2802476237032864], ['Dropout', 0.04764949831545384], ['Activate', 'sigmoid'], ['Maxpooling', 'Default'], ['Dense', 64], ['ZeroOp', 'Default'], ['conv', 64], ['Activate', 'selu'], ['Dense', 32], ['Activate', 'softmax'], ['Activate', 'elu'], ['conv', 8], ['Dropout', 0.05228122655810702], ['Dense', 16], ['ZeroOp', 'Default']]

Generation 10
(4, 15, 2)
Mutate 完成
Crossover完成
Modify_ResNet
[[3.         0.28024762]
 [2.         0.60421619]
 [4.         4.        ]
 [2.         0.39305468]
 [4.         2.        ]
 [1.         0.51889111]
 [0.         3.        ]
 [4.         3.        ]
 [5.         4.        ]
 [4.         0.        ]
 [4.         1.        ]
 [0.         0.        ]
 [3.         0.48069349]
 [5.         2.        ]
 [1.         0.81196033]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNor

Modify_ResNet
[[0.         5.        ]
 [1.         0.15660281]
 [4.         2.        ]
 [0.         5.        ]
 [5.         5.        ]
 [1.         0.22160605]
 [2.         0.26904391]
 [3.         0.08303601]
 [5.         0.        ]
 [0.         1.        ]
 [4.         1.        ]
 [0.         4.        ]
 [3.         0.05615965]
 [5.         2.        ]
 [4.         1.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
     

Modify_ResNet
[[3.         0.4722913 ]
 [2.         0.05436458]
 [5.         2.        ]
 [4.         3.        ]
 [5.         3.        ]
 [1.         0.57999823]
 [3.         0.03465458]
 [2.         0.20226234]
 [5.         3.        ]
 [1.         0.18592979]
 [0.         0.        ]
 [1.         0.04409989]
 [3.         0.02085367]
 [0.         5.        ]
 [4.         2.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
     

Modify_ResNet
[[3.         0.03519589]
 [2.         0.5224256 ]
 [4.         4.        ]
 [5.         1.        ]
 [5.         5.        ]
 [1.         0.08417292]
 [1.         0.17775081]
 [4.         2.        ]
 [5.         2.        ]
 [2.         0.54240058]
 [5.         3.        ]
 [0.         4.        ]
 [3.         0.0954441 ]
 [5.         5.        ]
 [0.         4.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
     

Select完成
Round Best:
0.260869562625885
structure is [['Dropout', 0.2802476237032864], ['Dropout', 0.04764949831545384], ['Activate', 'sigmoid'], ['Maxpooling', 'Default'], ['Dense', 64], ['ZeroOp', 'Default'], ['conv', 64], ['Activate', 'selu'], ['Dense', 32], ['Activate', 'softmax'], ['Activate', 'elu'], ['conv', 8], ['Dropout', 0.05228122655810702], ['Dense', 16], ['ZeroOp', 'Default']]


In [ ]:
# coding:UTF-8
# V2, ResNet Imporve
# 3.5.2022 run data, GPU


from __future__ import division
from numpy import *
import random as rd

NP = 4
size = 15
xMin = -10
xMax = 10
F = 0.8
CR = 0.5
LAYER_THRESHOLD = 0.9
GEN_MAX = 10
TRAIN_EPOCHES = 80

Convolution = [8, 16, 32, 64, 128, 256]
# ZeroOp, 默认
# MaxPooling, 默认
# Dropout, 0-0.5之间
# Activate = {1: 'softmax', 2: 'elu', 3: 'Relu', 4: 'selu', 5: 'sigmoid'}
Activate = ['softmax', 'elu', 'Relu', 'selu', 'sigmoid']
Dense = [4, 16, 32, 64, 128, 256]


# fetch data:
dsid = 'Adiac' 
bs = 64
X, y, splits = get_UCR_data(dsid, return_split=False)
print(X.shape)
tfms  = [None, [Categorize()]]
dsets = TSDatasets(X, y, tfms=tfms, splits=splits)
dls   = TSDataLoaders.from_dsets(dsets.train, dsets.valid, bs=[bs, bs*2])



# 完成
def translate_architecture(Individual, display=False):
    m, n = shape(Individual)
    Actual_structure = zeros((m, n))
    layers = []
    # 15 * 2
    for i in range(m):
        if Individual[i][0] == 0: # conv
            single_layer = ["conv"]
            single_layer.append(Convolution[int(Individual[i][1] * 6)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 6)]
        elif Individual[i][0] == 1: # ZeroOp
            single_layer = ["ZeroOp"]
            single_layer.append("Default")
            Actual_structure[i] = [Individual[i][0], Individual[i][1]]
        elif Individual[i][0] == 2: # Maxpooling
            single_layer = ["Maxpooling"]
            single_layer.append("Default")
            Actual_structure[i] = [Individual[i][0], Individual[i][1]]
        elif Individual[i][0] == 3:
            single_layer = ["Dropout"]
            single_layer.append(0.5*Individual[i][1])
            Actual_structure[i] = [Individual[i][0], 0.5*Individual[i][1]]
        elif Individual[i][0] == 4:
            single_layer = ["Activate"]
            single_layer.append(Activate[int(Individual[i][1] * 5)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 5)]
        elif Individual[i][0] == 5:
            single_layer = ["Dense"]
            single_layer.append(Dense[int(Individual[i][1] * 6)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 6)]
        layers.append(single_layer)
    if display:
        print(f"structure is {layers}")
    return Actual_structure


def GetModel(Phenotype):    
    m, n = shape(Phenotype)
    arch = Modify_ResNet
    print(arch.__name__)
    model = create_model(arch, dls=dls, Phenotype=Phenotype, batch_size=bs)
    print(model)
    return model


def getPred(Phenotype):
    
    # 训练
    model = GetModel(Phenotype)
    # return 1

    learn = Learner(dls, model,  metrics=accuracy)
    start = time.time()
    learn.fit_one_cycle(TRAIN_EPOCHES, 1e-3)
    elapsed = time.time() - start
    vals = learn.recorder.values[-1]
    # results = pd.DataFrame(columns=['arch', 'hyperparams', 'total params', 'train loss', 'valid loss', 'accuracy', 'time'])
    # results.loc[1] = [arch.__name__, {}, total_params(model)[0], vals[0], vals[1], vals[2], int(elapsed)]
    # results.sort_values(by='accuracy', ascending=False, ignore_index=True, inplace=True)
    # clear_output()
    # display(results)
    return vals[2]
    
    # return 1


# # 计算适应值函数
def calFitness(Individual):
    # Translate Individual Architecture
    # 目标: pred
    # Phenotype = translate_architecture(Individual, display=True)
    Phenotype = translate_architecture(Individual)


    # print("Phenotype after translate")
    # print(Phenotype)
    # 从getPred中获取对应的prediction
    fitness = getPred(Phenotype)

    return fitness



# 完成
def mutation(X_Parent, F, LAYER_THRESHOLD):
    # Mutate for Neural network
    print(shape(X_Parent))
    m, n, k = shape(X_Parent)
    # print()
    XMutationTmp = zeros((m, n, k))

    # 对于此时来说，需要额外设定一个layer_rate, 如果大于layer_rate，那么就mutate，layer，如果小于layer_rate，调整parameter。

    count = 0

    for i in range(m):
        r1 = 0
        r2 = 0
        r3 = 0
        while r1 == i or r2 == i or r3 == i or r1 == r2 or r1 == r3 or r2 == r3:
            r1 = rd.randint(0, m - 1)
            r2 = rd.randint(0, m - 1)
            r3 = rd.randint(0, m - 1)

        for j in range(n):
            # 如果需要修改layer
            layer_change = rd.random()
            if (layer_change > LAYER_THRESHOLD):
                changed_layer = rd.randint(0, 5)
                XMutationTmp[i, j] = [changed_layer, rd.random()]
                continue

            # 如果不需要修改layer， 这里会有点担心会产生越界

            # 首先要看一下此时是不是同一类的r1, r2, r3，因为真的太严格了，所以就是说mutate也要考虑基因突变
            # 如果r1、r2都满足的话，就可以按照操作开始变换。
            if X_Parent[r1, j, 0] == X_Parent[r2, j, 0] or X_Parent[r1, j, 0] == X_Parent[r3, j, 0]:
                # 用6完成一次取余操作
                XMutationTmp[i, j] = [X_Parent[r1, j, 0], (X_Parent[r1, j, 1] + F * (X_Parent[r2, j, 1] - X_Parent[r3, j, 1])) % 1]
                # print("差分操作完成", count)
                # count += 1
            else:
                XMutationTmp[i, j] = X_Parent[i, j]
    # print()
    return XMutationTmp


# 完成
def crossover(X_Parent, XMutationTmp, CR):
    # Binomial strategy
    # 按照CR crossrate完成修正增

    m, n, k = shape(X_Parent)
    X_Crossover = zeros((m, n, k))

    for i in range(m):
        for j in range(n):
            r = rd.random()
            if r <= CR:
                X_Crossover[i, j] = XMutationTmp[i, j]
            else:
                X_Crossover[i, j] = X_Parent[i, j]
    return X_Crossover


# 完成
def selection(X_Parent, XCrossover, fitnessVal):
    m, n, k = shape(X_Parent)
    print("Parent_fitness:", fitnessVal)
    fitnessCrossOverVal = zeros((m, 1))
    for i in range(m):
        print(f"第{i + 1}个变异个体")
        fitnessCrossOverVal[i, 0] = calFitness(XCrossover[i])
        if (fitnessCrossOverVal[i, 0] > fitnessVal[i, 0]):
            for j in range(n):
                X_Parent[i, j] = XCrossover[i, j]
            fitnessVal[i, 0] = fitnessCrossOverVal[i, 0]
    return X_Parent, fitnessVal


# 完成
def saveBest(XTemp, fitnessVal):
    m = shape(fitnessVal)[0]
    print("After selection", fitnessVal)
    tmp = 0
    for i in range(1, m):
        if (fitnessVal[tmp] < fitnessVal[i]):
            tmp = i

    print("Round Best:")
    print(fitnessVal[tmp][0])
    translate_architecture(XTemp[tmp], display=True)


# # 正文代码----------------

if __name__ == '__main__':

    # 初始化
    XTemp = zeros((NP, size, 2))
    # 构造对应的NP = 50, 基因长度size = 15, 每个size里包含的一个超参数，长度为2

    for i in range(NP):
        for j in range(size):
            # 初始化规则：对于每个XTemp[i, j]，[x, y]相当于初始化此时的类型x以及参数y
            # Conv的类型:          0; Conv的参数: [8, 16, 32, 64, 128, 256]; 一共6个参数，在乘以对应比例后截取整数部
            # ZeroOP的类型:        1; 没有参数
            # Maxpooling的类型:    2; MaxPooling，没有参数
            # Dropout的类型:       3; Dropout的参数: [0, 0.5]; random后乘以0.5
            # Activate的类型:      4; Activate的参数: ['softmax', 'elu', 'Relu', 'selu', 'sigmoid']; 5个参数，random后乘比例
            # Dense的类型:         5; Dense的参数: [4, 16, 32, 64, 128, 256]; 6个参数, random后乘比例。
            type = rd.randint(0, 5)
            XTemp[i, j] = [type, rd.random()]
    print("完成初始化")

    # 计算初始适应值
    fitnessVal = zeros((NP, 1))
    for i in range(NP):
        print(f"第{i + 1}个个体")
        fitnessVal[i, 0] = calFitness(XTemp[i])


    gen = 0
    while gen <= GEN_MAX:
        print("")
        print(f"Generation {gen}")
        # translate_architecture(XTemp[0], display=True)
        # mutate完成
        XMutationTmp = mutation(XTemp, F, LAYER_THRESHOLD)
        print("Mutate 完成")
        # translate_architecture(XMutationTmp[0], display=True)

        print("Crossover完成")
        XCrossover = crossover(XTemp, XMutationTmp, CR)
        # translate_architecture(XCrossover[0], display=True)

        XTemp, fitnessVal = selection(XTemp, XCrossover, fitnessVal)
        print("Select完成")
        # calFitness(XCrossover[0])
        saveBest(XTemp, fitnessVal)

        gen += 1

(781, 1, 176)
完成初始化
第0个个体
Modify_ResNet
[[1.         0.59325695]
 [3.         0.11002911]
 [3.         0.23971038]
 [0.         5.        ]
 [5.         5.        ]
 [3.         0.01964785]
 [3.         0.38155983]
 [1.         0.82664223]
 [2.         0.51167524]
 [1.         0.42367495]
 [4.         3.        ]
 [2.         0.81085064]
 [3.         0.00992197]
 [5.         3.        ]
 [0.         4.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), paddi

第1个个体
Modify_ResNet
[[0.         0.        ]
 [1.         0.87315901]
 [4.         4.        ]
 [4.         3.        ]
 [3.         0.11475284]
 [0.         2.        ]
 [0.         3.        ]
 [3.         0.34189859]
 [4.         1.        ]
 [0.         1.        ]
 [0.         5.        ]
 [2.         0.18950287]
 [0.         0.        ]
 [1.         0.49641091]
 [0.         3.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)

第2个个体
Modify_ResNet
[[4.         1.        ]
 [0.         3.        ]
 [2.         0.08565997]
 [3.         0.02403737]
 [2.         0.82188832]
 [3.         0.46581571]
 [3.         0.21391709]
 [1.         0.2883046 ]
 [3.         0.1073739 ]
 [3.         0.37214349]
 [0.         1.        ]
 [1.         0.66955425]
 [0.         0.        ]
 [4.         2.        ]
 [0.         3.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)

第3个个体
Modify_ResNet
[[2.         0.02193546]
 [2.         0.41040635]
 [3.         0.32563626]
 [1.         0.51871579]
 [2.         0.08754621]
 [5.         0.        ]
 [0.         1.        ]
 [5.         2.        ]
 [2.         0.85501444]
 [3.         0.35695247]
 [2.         0.18901113]
 [5.         2.        ]
 [1.         0.18307686]
 [1.         0.38317352]
 [1.         0.57132019]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)


Generation 0
(4, 15, 2)
Mutate 完成
Crossover完成
Parent_fitness: [[0.69565219]
 [0.24040921]
 [0.4961637 ]
 [0.40153453]]
第0个变异个体
Modify_ResNet
[[1.         0.59325695]
 [3.         0.11002911]
 [3.         0.23971038]
 [0.         5.        ]
 [2.         0.56145232]
 [3.         0.01964785]
 [0.         0.        ]
 [1.         0.82664223]
 [2.         0.51167524]
 [3.         0.08151543]
 [4.         3.        ]
 [2.         0.81085064]
 [3.         0.00992197]
 [1.         0.30699555]
 [0.         4.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): Re

...

Select完成
After selection [[0.71355498]
 [0.48337597]
 [0.69309461]
 [0.73145783]]
Round Best:
0.4833759665489197
structure is [['conv', 8], ['ZeroOp', 'Default'], ['Dropout', 0.46595539397486774], ['Activate', 'selu'], ['conv', 32], ['Dropout', 0.21175961626797135], ['conv', 64], ['ZeroOp', 'Default'], ['Activate', 'elu'], ['ZeroOp', 'Default'], ['conv', 256], ['Dropout', 0.014739687775473576], ['conv', 32], ['ZeroOp', 'Default'], ['conv', 64]]

Generation 10
(4, 15, 2)
Mutate 完成
Crossover完成
Parent_fitness: [[0.71355498]
 [0.48337597]
 [0.69309461]
 [0.73145783]]
第0个变异个体
Modify_ResNet
[[0.         1.        ]
 [3.         0.11002911]
 [3.         0.25265945]
 [0.         5.        ]
 [2.         0.13883763]
 [3.         0.01964785]
 [1.         0.26283789]
 [1.         0.85638943]
 [2.         0.51167524]
 [3.         0.13238951]
 [0.         4.        ]
 [2.         0.81085064]
 [0.         2.        ]
 [1.         0.45935149]
 [0.         4.        ]]
Modify_ResNet(
  (resblock1): Re

第1个变异个体
Modify_ResNet
[[0.         0.        ]
 [1.         0.87315901]
 [3.         0.46595539]
 [4.         3.        ]
 [2.         0.55136395]
 [3.         0.21175962]
 [0.         3.        ]
 [1.         0.57023871]
 [2.         0.02388855]
 [1.         0.7954653 ]
 [0.         4.        ]
 [3.         0.01473969]
 [0.         2.        ]
 [1.         0.44493956]
 [0.         3.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=Fals

第2个变异个体
Modify_ResNet
[[0.         4.        ]
 [0.         3.        ]
 [2.         0.08565997]
 [3.         0.02403737]
 [2.         0.45578694]
 [4.         2.        ]
 [0.         3.        ]
 [1.         0.04691023]
 [3.         0.1073739 ]
 [3.         0.16501365]
 [0.         2.        ]
 [1.         0.66955425]
 [0.         5.        ]
 [1.         0.50588193]
 [0.         4.        ]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=Fals

第3个变异个体
Modify_ResNet
[[0.         5.        ]
 [0.         1.        ]
 [3.         0.40121005]
 [1.         0.51871579]
 [2.         0.08754621]
 [5.         0.        ]
 [0.         1.        ]
 [1.         0.13956861]
 [2.         0.85501444]
 [3.         0.08441801]
 [0.         1.        ]
 [5.         2.        ]
 [0.         0.        ]
 [1.         0.49435238]
 [1.         0.57132019]]
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=Fals

Select完成
After selection [[0.71355498]
 [0.48337597]
 [0.76214832]
 [0.73145783]]
Round Best:
0.4833759665489197
structure is [['conv', 8], ['ZeroOp', 'Default'], ['Dropout', 0.46595539397486774], ['Activate', 'selu'], ['conv', 32], ['Dropout', 0.21175961626797135], ['conv', 64], ['ZeroOp', 'Default'], ['Activate', 'elu'], ['ZeroOp', 'Default'], ['conv', 256], ['Dropout', 0.014739687775473576], ['conv', 32], ['ZeroOp', 'Default'], ['conv', 64]]


In [ ]:
# coding:UTF-8
# V2, ResNet Imporve
# 3.5.2022 run2 data, GPU


from __future__ import division
from numpy import *
import random as rd

NP = 10                 # 群体个体数
F = 0.8                 # 变异率
CR = 0.5                # 交叉率
GEN_MAX = 10            # 进化轮次
LAYER_THRESHOLD = 0.9   # 变异修改神经元的类型的概率

TRAIN_EPOCHES = 100     # 训练轮数
size = 15               # 层数

Convolution = [8, 16, 32, 64, 128, 256]
# ZeroOp, 默认
# MaxPooling, 默认
# Dropout, 0-0.5之间
Activate = ['softmax', 'elu', 'Relu', 'selu', 'sigmoid']
Dense = [8, 16, 32, 64, 128, 256]

dsid = 'Adiac'

# fetch data:
bs = 64
X, y, splits = get_UCR_data(dsid, return_split=False)
print(X.shape)
tfms  = [None, [Categorize()]]
dsets = TSDatasets(X, y, tfms=tfms, splits=splits)
dls   = TSDataLoaders.from_dsets(dsets.train, dsets.valid, bs=[bs, bs*2])



# 完成
def translate_architecture(Individual, display=False):
    m, n = shape(Individual)
    Actual_structure = zeros((m, n))
    layers = []
    # 15 * 2
    for i in range(m):
        if Individual[i][0] == 0: # conv
            single_layer = ["conv"]
            single_layer.append(Convolution[int(Individual[i][1] * 6)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 6)]
        elif Individual[i][0] == 1: # ZeroOp
            single_layer = ["ZeroOp"]
            single_layer.append("Default")
            Actual_structure[i] = [Individual[i][0], Individual[i][1]]
        elif Individual[i][0] == 2: # Maxpooling
            single_layer = ["Maxpooling"]
            single_layer.append("Default")
            Actual_structure[i] = [Individual[i][0], Individual[i][1]]
        elif Individual[i][0] == 3:
            single_layer = ["Dropout"]
            single_layer.append(0.5*Individual[i][1])
            Actual_structure[i] = [Individual[i][0], 0.5*Individual[i][1]]
        elif Individual[i][0] == 4:
            single_layer = ["Activate"]
            single_layer.append(Activate[int(Individual[i][1] * 5)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 5)]
        elif Individual[i][0] == 5:
            single_layer = ["Dense"]
            single_layer.append(Dense[int(Individual[i][1] * 6)])
            Actual_structure[i] = [Individual[i][0], int(Individual[i][1] * 6)]
        layers.append(single_layer)
    if display:
        print(f"structure is {layers}")
    return Actual_structure


def GetModel(Phenotype):    
    m, n = shape(Phenotype)
    arch = Modify_ResNet
    print(arch.__name__)
    model = create_model(arch, dls=dls, Phenotype=Phenotype, batch_size=bs)
    print(model)
    return model


def getPred(Phenotype):
    
    # 训练
    model = GetModel(Phenotype)
    # return 1

    learn = Learner(dls, model,  metrics=accuracy)
    start = time.time()
    learn.fit_one_cycle(TRAIN_EPOCHES, 1e-3)
    elapsed = time.time() - start
    vals = learn.recorder.values[-1]
    # results = pd.DataFrame(columns=['arch', 'hyperparams', 'total params', 'train loss', 'valid loss', 'accuracy', 'time'])
    # results.loc[1] = [arch.__name__, {}, total_params(model)[0], vals[0], vals[1], vals[2], int(elapsed)]
    # results.sort_values(by='accuracy', ascending=False, ignore_index=True, inplace=True)
    # clear_output()
    # display(results)
    return vals[2]
    
    # return 1


# # 计算适应值函数
def calFitness(Individual):
    # Translate Individual Architecture
    # 目标: pred
    # Phenotype = translate_architecture(Individual, display=True)
    Phenotype = translate_architecture(Individual)


    # print("Phenotype after translate")
    # print(Phenotype)
    # 从getPred中获取对应的prediction
    fitness = getPred(Phenotype)

    return fitness



# 完成
def mutation(X_Parent, F, LAYER_THRESHOLD):
    # Mutate for Neural network
    print(shape(X_Parent))
    m, n, k = shape(X_Parent)
    # print()
    XMutationTmp = zeros((m, n, k))

    # 对于此时来说，需要额外设定一个layer_rate, 如果大于layer_rate，那么就mutate，layer，如果小于layer_rate，调整parameter。

    count = 0

    for i in range(m):
        r1 = 0
        r2 = 0
        r3 = 0
        while r1 == i or r2 == i or r3 == i or r1 == r2 or r1 == r3 or r2 == r3:
            r1 = rd.randint(0, m - 1)
            r2 = rd.randint(0, m - 1)
            r3 = rd.randint(0, m - 1)

        for j in range(n):
            # 如果需要修改layer
            layer_change = rd.random()
            if (layer_change > LAYER_THRESHOLD):
                changed_layer = rd.randint(0, 5)
                XMutationTmp[i, j] = [changed_layer, rd.random()]
                continue

            # 如果不需要修改layer， 这里会有点担心会产生越界

            # 首先要看一下此时是不是同一类的r1, r2, r3，因为真的太严格了，所以就是说mutate也要考虑基因突变
            # 如果r1、r2都满足的话，就可以按照操作开始变换。
            if X_Parent[r1, j, 0] == X_Parent[r2, j, 0] or X_Parent[r1, j, 0] == X_Parent[r3, j, 0]:
                # 用6完成一次取余操作
                XMutationTmp[i, j] = [X_Parent[r1, j, 0], (X_Parent[r1, j, 1] + F * (X_Parent[r2, j, 1] - X_Parent[r3, j, 1])) % 1]
                # print("差分操作完成", count)
                # count += 1
            else:
                XMutationTmp[i, j] = X_Parent[i, j]
    # print()
    return XMutationTmp


# 完成
def crossover(X_Parent, XMutationTmp, CR):
    # Binomial strategy
    # 按照CR crossrate完成修正增

    m, n, k = shape(X_Parent)
    X_Crossover = zeros((m, n, k))

    for i in range(m):
        for j in range(n):
            r = rd.random()
            if r <= CR:
                X_Crossover[i, j] = XMutationTmp[i, j]
            else:
                X_Crossover[i, j] = X_Parent[i, j]
    return X_Crossover


# 完成
def selection(X_Parent, XCrossover, fitnessVal):
    m, n, k = shape(X_Parent)
    print("Parent_fitness:", fitnessVal)
    fitnessCrossOverVal = zeros((m, 1))
    for i in range(m):
        print(f"第{i + 1}个变异个体")
        fitnessCrossOverVal[i, 0] = calFitness(XCrossover[i])
        if (fitnessCrossOverVal[i, 0] > fitnessVal[i, 0]):
            print("Mutate better")
            for j in range(n):
                X_Parent[i, j] = XCrossover[i, j]
            fitnessVal[i, 0] = fitnessCrossOverVal[i, 0]
        else:    
            print("Parent Better")
    return X_Parent, fitnessVal


# 完成
def saveBest(XTemp, fitnessVal):
    m = shape(fitnessVal)[0]
    print("After selection", fitnessVal)
    tmp = 0
    for i in range(1, m):
        if (fitnessVal[tmp] < fitnessVal[i]):
            tmp = i

    print("Round Best:")
    print(fitnessVal[tmp][0])
    translate_architecture(XTemp[tmp], display=True)


# # 正文代码----------------

if __name__ == '__main__':

    # 初始化
    XTemp = zeros((NP, size, 2))
    # 构造对应的NP = 50, 基因长度size = 15, 每个size里包含的一个超参数，长度为2

    for i in range(NP):
        for j in range(size):
            # 初始化规则：对于每个XTemp[i, j]，[x, y]相当于初始化此时的类型x以及参数y
            # Conv的类型:          0; Conv的参数: [8, 16, 32, 64, 128, 256]; 一共6个参数，在乘以对应比例后截取整数部
            # ZeroOP的类型:        1; 没有参数
            # Maxpooling的类型:    2; MaxPooling，没有参数
            # Dropout的类型:       3; Dropout的参数: [0, 0.5]; random后乘以0.5
            # Activate的类型:      4; Activate的参数: ['softmax', 'elu', 'Relu', 'selu', 'sigmoid']; 5个参数，random后乘比例
            # Dense的类型:         5; Dense的参数: [4, 16, 32, 64, 128, 256]; 6个参数, random后乘比例。
            type = rd.randint(0, 5)
            XTemp[i, j] = [type, rd.random()]
    print("完成初始化")

    # 计算初始适应值
    fitnessVal = zeros((NP, 1))
    for i in range(NP):
        print(f"第{i + 1}个个体")
        fitnessVal[i, 0] = calFitness(XTemp[i])


    gen = 0
    while gen <= GEN_MAX:
        print("")
        print(f"Generation {gen}")
        # translate_architecture(XTemp[0], display=True)
        # mutate完成
        XMutationTmp = mutation(XTemp, F, LAYER_THRESHOLD)
        print("Mutate 完成")
        # translate_architecture(XMutationTmp[0], display=True)

        print("Crossover完成")
        XCrossover = crossover(XTemp, XMutationTmp, CR)
        # translate_architecture(XCrossover[0], display=True)

        XTemp, fitnessVal = selection(XTemp, XCrossover, fitnessVal)
        print("Select完成")
        # calFitness(XCrossover[0])
        saveBest(XTemp, fitnessVal)

        gen += 1

(781, 1, 176)
完成初始化
第1个个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    

第2个个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (convblock1): ConvBl

第3个个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (convblock1): ConvBl

第4个个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (convblock1): ConvBl

第5个个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (convblock1): ConvBl

...

Parent Better
第7个变异个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (con

Mutate better
第8个变异个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (con

Parent Better
第9个变异个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (con

Parent Better
第10个变异个体
Modify_ResNet
Modify_ResNet(
  (resblock1): ResBlock(
    (convblock1): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(7,), stride=(1,), padding=(3,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock2): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(5,), stride=(1,), padding=(2,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU()
    )
    (convblock3): ConvBlock(
      (0): Conv1d(64, 64, kernel_size=(3,), stride=(1,), padding=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (shortcut): ConvBlock(
      (0): Conv1d(1, 64, kernel_size=(1,), stride=(1,), bias=False)
      (1): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (add): Add
    (act): ReLU()
  )
  (resblock2): ResBlock(
    (co

Parent Better
Select完成
After selection [[0.7647059 ]
 [0.76982099]
 [0.75703323]
 [0.58056265]
 [0.80818415]
 [0.79795396]
 [0.79795396]
 [0.7723785 ]
 [0.83120203]
 [0.75703323]]
Round Best:
0.5805626511573792
structure is [['Dense', 16], ['Dropout', 0.05409201844954831], ['Dense', 128], ['Activate', 'selu'], ['Maxpooling', 'Default'], ['Maxpooling', 'Default'], ['Dense', 256], ['conv', 256], ['conv', 256], ['Activate', 'Relu'], ['Activate', 'Relu'], ['Dropout', 0.014500294802382185], ['Dense', 128], ['Dropout', 0.45598086730065], ['conv', 16]]
